In [1]:
import geopandas as gpd
import json
import pandas as pd
from pathlib import Path
import pandas as pd
import requests as r
from fuzzywuzzy import process
import re
import numpy as np
from tqdm import tqdm
from shapely.geometry import Polygon

In [2]:
DATA_PATH = Path("/home/riccardofiorista/Documents/courses/6.C85/fp_code/data")
OUTPUT_PATH = DATA_PATH / "preprocessed_data"

# Municipalities

In [44]:
gdf = gpd.read_file(DATA_PATH / "CENSUS2020TOWNS_SHP/CENSUS2020TOWNS_POLY.shp", crs="EPSG:26986")

In [45]:
gdf.columns

Index(['STATEFP20', 'COUNTYFP20', 'COUSUBFP20', 'COUSUBNS20', 'GEOID20',
       'NAMELSAD20', 'LSAD20', 'CLASSFP20', 'MTFCC20', 'CNECTAFP20',
       'NECTAFP20', 'NCTADVFP20', 'FUNCSTAT20', 'ALAND20', 'AWATER20',
       'INTPTLAT20', 'INTPTLON20', 'TOWN20', 'TOWN_ID', 'FIPS_STCO2',
       'COUNTY20', 'TYPE', 'FOURCOLOR', 'AREA_ACRES', 'SQ_MILES', 'POP1960',
       'POP1970', 'POP1980', 'POP1990', 'POP2000', 'POP2010', 'POP2020',
       'POPCH10_20', 'HOUSING20', 'SHAPE_AREA', 'SHAPE_LEN', 'geometry'],
      dtype='object')

In [46]:
gdf[['NAMELSAD20', 'HOUSING20', 'geometry', 'SQ_MILES', 'POP2020', 'AREA_ACRES', 'FOURCOLOR', 'TYPE', 'ALAND20']].head(5)

NAMELSAD20  HOUSING20  \
0        Lenox town       3184   
1  New Ashford town        126   
2         Otis town       1609   
3     Hatfield town       1634   
4     Charlton town       5239   

                                            geometry  SQ_MILES  POP2020  \
0  POLYGON ((58247.441 906994.426, 58033.789 9060...     21.67     5095   
1  POLYGON ((62892.770 932247.060, 62868.927 9319...     13.47      250   
2  POLYGON ((75550.344 888649.854, 75514.833 8884...     38.05     1634   
3  POLYGON ((111026.434 908570.805, 111029.370 90...     16.82     3352   
4  POLYGON ((166144.326 871286.918, 166106.465 87...     43.79    13315   

   AREA_ACRES  FOURCOLOR TYPE      ALAND20  
0    13866.45          3    T   54950826.0  
1     8623.50          1    T   34862609.0  
2    24354.37          4    T   92103734.0  
3    10766.48          4    T   41175416.0  
4    28025.52          3    T  109242811.0

In [47]:
filtered_gdf = gdf[['NAMELSAD20', 'HOUSING20', 'SQ_MILES', 'POP2020', 'AREA_ACRES', 'TYPE', 'ALAND20', 'geometry']].copy(deep=True)
filtered_gdf['NAMELSAD20'] = filtered_gdf['NAMELSAD20'].str.lower().str.replace(' town', '').str.replace(' city', '').str.title()
filtered_gdf['COMMUNITY'] = filtered_gdf['NAMELSAD20']
filtered_gdf = filtered_gdf.dropna()

In [48]:
mbta_communities_df = pd.read_excel(DATA_PATH / 'MBTA Communities - Cohort Designations and Capacity Calculations.xlsx')
mbta_communities_df = mbta_communities_df.dropna()

In [49]:
mbtac_gdf = mbta_communities_df.merge(filtered_gdf, left_on='Municipality', right_on='COMMUNITY', how='left')
mbtac_gdf['MBTA_COMM_TYPE'] = mbtac_gdf['MBTA Community Type']
mbtac_gdf['HOUSING_UNITS_2020'] = mbtac_gdf['2020 Housing Units \n(Census PL-94)']
mbtac_gdf['MIN_RF1_CAP_REQ'] = mbtac_gdf['Minimum multifamily district unit capacity requirement']
mbtac_gdf = mbtac_gdf.drop(columns=['MBTA Community Type', '2020 Housing Units \n(Census PL-94)', 'Minimum multifamily district unit capacity requirement'])
mbtac_gdf.columns = [c.lower() for c in mbtac_gdf.columns]
mbtac_gdf = gpd.GeoDataFrame(mbtac_gdf, crs=filtered_gdf.crs)

In [115]:
mbtac_gdf.explore()

In [116]:
mbtac_gdf.head(5)

municipality namelsad20  housing20  sq_miles  pop2020  area_acres type  \
0     Abington   Abington     6811.0     10.19  17062.0     6520.85    T   
1        Acton      Acton     9219.0     20.30  24021.0    12989.35    T   
2     Amesbury   Amesbury     7889.0     13.73  17366.0     8788.93    C   
3      Andover    Andover    13541.0     32.15  36569.0    20578.09    T   
4    Arlington  Arlington    20461.0      5.49  46308.0     3510.40    T   

      aland20                                           geometry  community  \
0  25795965.0  POLYGON ((248314.516 872355.441, 248301.966 87...   Abington   
1  51453349.0  POLYGON ((209455.542 917109.043, 209452.756 91...      Acton   
2  31836415.0  POLYGON ((248713.789 953867.270, 248652.758 95...   Amesbury   
3  79811403.0  POLYGON ((225495.093 938455.256, 225495.429 93...    Andover   
4  13319999.0  POLYGON ((228807.569 909538.834, 228868.316 90...  Arlington   

         mbta_comm_type  housing_units_2020  min_rf1_cap_req  
0         commuter rail                6811          1021.65  
1         commuter rail                9219          1382.85  
2         MBTA adjacent                7889           788.90  
3         commuter rail               13541          2031.15  
4  subway or light rail               20461          5115.25

In [117]:
mbtac_gdf_to_save = mbtac_gdf.copy(deep=True)
mbtac_gdf_to_save = mbtac_gdf_to_save.to_crs('EPSG:4326')
mbtac_gdf.to_file(OUTPUT_PATH / "mbta_municipalities.geojson")

# MBTA

## Stops

In [50]:
stops_gdf = gpd.read_file(DATA_PATH / "mbta_stops_only.geojson")
# Need to project because mbtac is in this projection and then we can also work with meters
stops_gdf = stops_gdf.to_crs(mbtac_gdf.crs)  # "EPSG:26986"
stops_gdf['routes'] = stops_gdf['routes'].apply(json.loads)

In [51]:
zone_ids_to_include = [
    # 'ExpressBus-Downtown',
    # 'LocalBus',
    'RapidTransit',
    'SL1-Logan',
    'SLWaterfrontNonLogan',
    'CR-zone-1A',
    # 'None',
    'Boat-Hingham',
    'Boat-Hull',
    'Boat-Logan',
    'Boat-Long',
    'Boat-Rowes',
    # 'CF-zone-buzzards',
    # 'CF-zone-hyannis',
    'CR-zone-2',
    'CR-zone-3',
    'CR-zone-4',
    'CR-zone-5',
    'CR-zone-6',
    'CR-zone-7',
    'CR-zone-8',
    'CR-zone-1',
    'CR-zone-10',
    'CR-zone-9',
]
filtered_stops = stops_gdf[stops_gdf['zone_id'].isin(zone_ids_to_include)].copy(deep=True).reset_index(drop=True)

In [52]:
filtered_stops[[c for c in filtered_stops if c != 'routes']].explore(color='red')

In [53]:
filtered_stops['route_colors'] = filtered_stops['routes'].apply(lambda x: [e['route_color'] for e in x])

In [54]:
def compute_centroid(group):
    return group.unary_union.centroid

def aggregate_routes(group):
    # This function aggregates 'route_short_name' from the 'routes' arrays of dicts
    # into a flat list for each group
    routes = []
    for array in group.to_list():
        for item in array:
            if 'route_short_name' in item:
                routes.append(item['route_short_name'])
            elif 'route_long_name' in item:
                routes.append(item['route_long_name'])
    return list(set(routes))  # Return unique 'route_short_name'

def aggregate_route_colors(group):
    # This function aggregates 'route_short_name' from the 'routes' arrays of dicts
    # into a flat list for each group
    route_colors = []
    for array in group.to_list():
        for item in array:
            route_colors.append(item)
    return list(set(route_colors))  # Return unique 'route_short_name'

aggregations = {
    'geometry': compute_centroid,
    'zone_id': lambda x: list(set(x)),
    'routes': aggregate_routes,
    'route_colors': aggregate_route_colors,
}
midpoints = filtered_stops.groupby('stop_name').agg(aggregations).reset_index()
midpoints = gpd.GeoDataFrame(midpoints, geometry='geometry', crs=filtered_stops.crs)

In [55]:
points_within_polygons = gpd.sjoin(midpoints, mbtac_gdf, predicate='within')
points_within_polygons = points_within_polygons.drop(columns='index_right')

In [124]:
points_within_polygons.explore(color='red')

In [125]:
mbta_community_stops = points_within_polygons.copy(deep=True)
mbta_community_stops = mbta_community_stops.to_crs('EPSG:4326')
mbta_community_stops['zone_id'] = mbta_community_stops['zone_id'].apply(json.dumps)
mbta_community_stops['routes'] = mbta_community_stops['routes'].apply(json.dumps)
mbta_community_stops['route_colors'] = mbta_community_stops['route_colors'].apply(json.dumps)
mbta_community_stops.to_file(OUTPUT_PATH / "mbta_community_stops.geojson", driver='GeoJSON')

## Lines

In [126]:
lines_gdf = gpd.read_file(DATA_PATH / "mbta_lines.geojson")
# Same reprojection as above
lines_gdf = lines_gdf.to_crs(mbtac_gdf.crs)  # "EPSG:26986"

In [127]:
lines_gdf.head(5)

agency_name route_id agency_id route_short_name  \
0        MBTA      716         1              716   
1        MBTA      716         1              716   
2        MBTA      716         1              716   
3        MBTA      716         1              716   
4        MBTA      716         1              716   

                   route_long_name route_desc  route_type  \
0  Cobbs Corner - Mattapan Station  Local Bus           3   
1  Cobbs Corner - Mattapan Station  Local Bus           3   
2  Cobbs Corner - Mattapan Station  Local Bus           3   
3  Cobbs Corner - Mattapan Station  Local Bus           3   
4  Cobbs Corner - Mattapan Station  Local Bus           3   

                            route_url route_color route_text_color  \
0  https://www.mbta.com/schedules/716     #FFC72C          #000000   
1  https://www.mbta.com/schedules/716     #FFC72C          #000000   
2  https://www.mbta.com/schedules/716     #FFC72C          #000000   
3  https://www.mbta.com/schedules/716     #FFC72C          #000000   
4  https://www.mbta.com/schedules/716     #FFC72C          #000000   

   route_sort_order            network_id  \
0             57160  local_bus_restricted   
1             57160  local_bus_restricted   
2             57160  local_bus_restricted   
3             57160  local_bus_restricted   
4             57160  local_bus_restricted   

                                            geometry  
0  LINESTRING (229330.347 876752.426, 229389.048 ...  
1  LINESTRING (230584.862 884258.570, 230638.551 ...  
2  LINESTRING (230985.480 884232.552, 231007.776 ...  
3  LINESTRING (233653.966 890888.208, 233719.060 ...  
4  LINESTRING (233446.030 890548.435, 233354.806 ...

In [128]:
lines_gdf['route_desc'].unique()

array(['Local Bus', 'Commuter Bus', 'Supplemental Bus', 'Key Bus',
       'Community Bus', 'Ferry', 'Commuter Rail', 'Rapid Transit'],
      dtype=object)

In [129]:
# First round of filtering depending on the route description 
route_desc_to_keep = [
    # "Local Bus",
    # "Commuter Bus",
    # "Supplemental Bus",
    "Key Bus",
    # "Community Bus",
    "Ferry",
    "Commuter Rail",
    "Rapid Transit",
]
filtered_lines = lines_gdf[lines_gdf['route_desc'].isin(route_desc_to_keep)].copy(deep=True)

In [130]:
# Replace NaN values with empty string
filtered_lines.loc[filtered_lines['route_short_name'].isna(), 'route_short_name'] = ''

In [131]:
# Get all the SL bus route IDs
filtered_lines[filtered_lines['route_short_name'].str.contains('SL')]['route_id'].unique()

array(['746', '749', '751', '743', '742', '741'], dtype=object)

In [132]:
route_ids_to_keep = [
    # "117",
    # "116",
    # "111",
    # "77",
    # "73",
    # "71",
    # "66",
    # "57",
    # "39",
    # "32",
    # "28",
    # "23",
    # "22",
    # "15",
    # "1",
    "Boat-F1",
    "Boat-F4",
    # "CapeFlyer",
    "CR-Foxboro",
    "CR-Providence",
    "CR-Newburyport",
    "CR-Needham",
    "CR-Middleborough",
    "CR-Lowell",
    "CR-Kingston",
    "CR-Haverhill",
    "CR-Greenbush",
    "CR-Franklin",
    "CR-Worcester",
    "CR-Fitchburg",
    "CR-Fairmount",
    # SL BUSSES ######
    "746",
    "749",
    "751",
    "743",
    "742",
    "741",
    ##################
    "Blue",
    "Green-E",
    "Green-D",
    "Green-C",
    "Green-B",
    "Orange",
    "Mattapan",
    "Red",
]

filtered_lines = lines_gdf[lines_gdf['route_id'].isin(route_ids_to_keep)].copy(deep=True)

In [133]:
filtered_lines.explore(color=filtered_lines['route_color'])

In [134]:
# TODO Clip lines to MBTA Community polygon exterior
# complete_region_boundary = mbtac_gdf.unary_union.boundary
# mega_polygon_no_holes = gpd.GeoSeries(complete_region_boundary).unary_union
# intersected_lines = filtered_lines['geometry'].intersection(mega_polygon_no_holes)
# 
# # Replace the old geometry with the new intersected geometries
# filtered_lines['geometry'] = intersected_lines
# 
# # Remove empty geometries if they don't intersect with the convex hull at all
# filtered_lines = filtered_lines[~filtered_lines['geometry'].is_empty]

In [135]:
# lines_within_polygons = gpd.sjoin(filtered_lines, mbtac_gdf, predicate='within')

In [136]:
mbta_community_lines = filtered_lines.copy(deep=True)
mbta_community_lines = mbta_community_lines.to_crs('EPSG:4326')
mbta_community_lines.to_file(OUTPUT_PATH / "mbta_community_lines.geojson", driver='GeoJSON')

# Parcel Data

In [10]:
parcel_zoning_links = pd.read_excel(DATA_PATH / 'MassGIS_Parcel_Download_Links.xlsx')

/home/riccardofiorista/anaconda3/envs/data_vis/lib/python3.11/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")


In [11]:
parcel_zoning_links['Town Name'] = parcel_zoning_links['Town Name'].str.title()

In [12]:
links_for_mbta_communities = parcel_zoning_links[parcel_zoning_links['Town Name'].isin(mbtac_gdf['municipality'])]

mbta_community_parcels_path = DATA_PATH / 'parcels_per_municipality'
for i, entry in tqdm(links_for_mbta_communities.iterrows()):
    link = entry['Shapefile Download URL']
    municipality = entry['Town Name']
    output_path = DATA_PATH / 'parcels_per_municipality' / f'{municipality}.zip'
    
    if not output_path.exists():
        response = r.get(link)
        
        if response.status_code == 200:
            with output_path.open(mode='wb') as file:
                file.write(response.content)
                

175it [00:00, 12724.33it/s]


In [13]:
folders = [entry for entry in mbta_community_parcels_path.glob('*') if entry.is_dir()]
first_subfolders = []

for folder in folders:
    subfolders = [subfolder for subfolder in folder.iterdir() if subfolder.is_dir()]
    if subfolders:  # Make sure the list is not empty
        first_subfolders.append(subfolders[0])
    else:
        first_subfolders.append(None)  # Or some placeholder to indicate no subfolders are present

In [22]:
shape_files = [list(f.glob('*TaxPar*.shp'))[0] for f in first_subfolders]

In [34]:
# Initialize an empty list to store individual GeoDataFrames
gdfs = []

# Iterate over each shapefile path
for shp_path in tqdm(shape_files):
    # Load the shapefile into a GeoDataFrame
    gdf = gpd.read_file(shp_path)
    town_name = shp_path.parent.parent.name
    gdf['TOWN_NAME'] = town_name
    gdf['TOWN_ID'] = links_for_mbta_communities[links_for_mbta_communities['Town Name'] == town_name]['Town ID'].values[0]
    gdf['ASSESSED_FY'] = links_for_mbta_communities[links_for_mbta_communities['Town Name'] == town_name]['Assessed Fiscal Year'].values[0]
    
    # Add the loaded GeoDataFrame to the list
    gdfs.append(gdf)

# Concatenate all GeoDataFrames in the list into a single GeoDataFrame
all_gdfs = gpd.GeoDataFrame(pd.concat(gdfs, ignore_index=True)) 

100%|██████████| 175/175 [04:16<00:00,  1.47s/it]


In [35]:
parcel_layer_data = pd.read_csv(DATA_PATH / 'L3_TAXPAR_POLY_ASSESS_gdb_features_all.csv')

/tmp/ipykernel_29300/3326588884.py:1: DtypeWarning: Columns (4,8,10,15,17,19,20,26,35,37,39,40,42,44) have mixed types. Specify dtype option on import or set low_memory=False.
  parcel_layer_data = pd.read_csv(DATA_PATH / 'L3_TAXPAR_POLY_ASSESS_gdb_features_all.csv')


In [37]:
full_parcel_gdf = pd.merge(all_gdfs, parcel_layer_data, left_on='LOC_ID', right_on='LOC_ID', suffixes=('_muni', '_tax'))

In [38]:
full_parcel_gdf = full_parcel_gdf.fillna(value=np.nan)

In [39]:
full_parcel_gdf = full_parcel_gdf.drop(
    columns=['LAST_EDIT_muni', 'NO_MATCH_muni', 'POLY_TYPE_muni', 'SOURCE_tax',
             'MAP_NO_muni', 'SOURCE_muni', 'PLAN_ID_muni', 'BND_CHK_muni', 'TOWN_ID_muni',
             'MAP_PAR_ID_muni']
)
full_parcel_gdf.columns = [c.replace('_tax','') for c in full_parcel_gdf.columns]

In [ ]:
full_parcel_gdf_to_save = full_parcel_gdf.copy(deep=True)
full_parcel_gdf_to_save = full_parcel_gdf.to_crs('EPSG:4326')
# Uncomment only if you're really sure you want to do this
full_parcel_gdf_to_save.to_file(OUTPUT_PATH / "complete_parcels.geojson", driver='GeoJSON')

# Cut Parcels to Stations

In [56]:
stations_with_buffer = points_within_polygons.copy(deep=True)
# Add half a mile buffer to stations in meters (as radius)
stations_with_buffer['geometry'] = points_within_polygons.buffer(804.67)

In [57]:
station_only_parcels = gpd.sjoin(full_parcel_gdf, stations_with_buffer, predicate='within')

In [60]:
station_only_parcels = station_only_parcels.drop(columns='index_right')

In [62]:
station_only_parcels.head(5)

SHAPE_Leng   SHAPE_Area            LOC_ID  \
16259   89.635545   481.344116  F_742210_2868033   
16281  155.500208  1026.109183  F_741690_2868045   
16305  191.535315  1733.381189  F_742188_2868127   
16314  211.469655  2357.588003  F_741945_2868130   
16316  164.853680  1386.541407  F_742096_2868127   

                                                geometry TOWN_NAME  \
16259  POLYGON ((226240.172 874184.625, 226238.797 87...    Sharon   
16281  POLYGON ((226087.484 874188.750, 226087.109 87...    Sharon   
16305  POLYGON ((226240.172 874184.625, 226224.125 87...    Sharon   
16314  POLYGON ((226153.781 874228.250, 226173.984 87...    Sharon   
16316  POLYGON ((226215.125 874227.938, 226213.906 87...    Sharon   

       ASSESSED_FY  Shape_Leng  Shape_Area   OBJECTID MAP_PAR_ID  ...  \
16259         2023         NaN         NaN  1286608.0       91_4  ...   
16281         2023         NaN         NaN  1057028.0      91_12  ...   
16305         2023         NaN         NaN  2009443.0       91_5  ...   
16314         2023         NaN         NaN   476479.0       91_9  ...   
16316         2023         NaN         NaN   477441.0       91_6  ...   

      housing20 sq_miles  pop2020  area_acres type     aland20 community  \
16259    6581.0    24.39  18575.0    15608.24    T  60697096.0    Sharon   
16281    6581.0    24.39  18575.0    15608.24    T  60697096.0    Sharon   
16305    6581.0    24.39  18575.0    15608.24    T  60697096.0    Sharon   
16314    6581.0    24.39  18575.0    15608.24    T  60697096.0    Sharon   
16316    6581.0    24.39  18575.0    15608.24    T  60697096.0    Sharon   

      mbta_comm_type  housing_units_2020  min_rf1_cap_req  
16259  commuter rail                6581           987.15  
16281  commuter rail                6581           987.15  
16305  commuter rail                6581           987.15  
16314  commuter rail                6581           987.15  
16316  commuter rail                6581           987.15  

[5 rows x 70 columns]

In [ ]:
station_only_parcels_to_save = station_only_parcels.copy(deep=True)
station_only_parcels_to_save = station_only_parcels_to_save.copy(deep=True)
station_only_parcels_to_save = station_only_parcels_to_save.to_crs('EPSG:4326')
station_only_parcels_to_save['zone_id'] = station_only_parcels_to_save['zone_id'].apply(json.dumps)
station_only_parcels_to_save['routes'] = station_only_parcels_to_save['routes'].apply(json.dumps)
station_only_parcels_to_save['route_colors'] = station_only_parcels_to_save['route_colors'].apply(json.dumps)
# Uncomment only if you're really sure you want to do this
station_only_parcels_to_save.to_file(OUTPUT_PATH / "station_only_parcels.geojson", driver='GeoJSON')